In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
#import necessary libraries
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import GridSearchCV
from sklearn.feature_selection import RFECV
from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error, r2_score

In [3]:
pd.set_option('max_colwidth', None)
var=pd.read_csv('/content/drive/MyDrive/fire-extent-prediction-challenge-120240716-19716-ztmgh3/variable_definitions.csv')
var

Variable  \
0              ID   
1            area   
2            date   
3             lat   
4             lon   
5       burn_area   
6     climate_aet   
7     climate_def   
8    climate_pdsi   
9     climate_pet   
10     climate_pr   
11     climate_ro   
12   climate_soil   
13   climate_srad   
14    climate_swe   
15   climate_tmmn   
16   climate_tmmx   
17    climate_vap   
18    climate_vpd   
19     climate_vs   
20      elevation   
21    landcover_0   
22    landcover_1   
23    landcover_2   
24    landcover_3   
25    landcover_4   
26    landcover_5   
27    landcover_6   
28    landcover_7   
29    landcover_8   
30  precipitation   

                                                                                                                                  Description  
0                      The IDs take the form of [area ID]_yyyy-mm-dd. There are 533 area squares each with a unique ID ranging from 0 to 532.  
1                                                                                                                                     Area ID  
2                                                                                                   The date that the data is aggregated over  
3                                                                                                          Latitude of the center of the area  
4                                                                                                         Longitude of the center of the area  
5                                                                                                                Percentage of the area burnt  
6                                                         Actual evapotranspiration, derived using a one-dimensional soil water balance model  
7                                                             Climate water deficit, derived using a one-dimensional soil water balance model  
8                                                                                                               Palmer Drought Severity Index  
9                                                                                         Reference evapotranspiration (ASCE Penman-Montieth)  
10                                                                                                                 Precipitation accumulation  
11                                                                           Runoff, derived using a one-dimensional soil water balance model  
12                                                                    Soil moisture, derived using a one-dimensional soil water balance model  
13                                                                                                       Downward surface shortwave radiation  
14                                                            Snow water equivalent, derived using a one-dimensional soil water balance model  
15                                                                                                                        Minimum temperature  
16                                                                                                                        Maximum temperature  
17                                                                                                                             Vapor pressure  
18                                                                                                                     Vapor pressure deficit  
19                                                                                                                          Wind-speed at 10m  
20                                                                                                                             Land elevation  
21                                                                   Water Bodies: at least 60% of area is covered by permanent water bodies.  
22                     E

In [4]:
train=pd.read_csv('/content/drive/MyDrive/fire-extent-prediction-challenge-120240716-19716-ztmgh3/Train.csv')

In [5]:
pd.set_option('display.max_columns', None)
train

ID        lat        lon  burn_area  climate_aet  \
0        0_2001-01-01 -15.858835  29.237029        0.0         1195   
1        1_2001-01-01 -15.858835  29.487029        0.0         1196   
2        2_2001-01-01 -15.858835  29.737029        0.0         1190   
3        3_2001-01-01 -15.858835  29.987029        0.0         1144   
4        4_2001-01-01 -15.858835  30.237029        0.0         1187   
...               ...        ...        ...        ...          ...   
83143  528_2013-12-01 -22.108835  30.737029        0.0         1210   
83144  529_2013-12-01 -22.108835  30.987029        0.0         1295   
83145  530_2013-12-01 -22.108835  31.237029        0.0         1254   
83146  531_2013-12-01 -22.108835  31.487029        0.0         1221   
83147  532_2013-12-01 -22.358835  31.237029        0.0         1132   

       climate_def  climate_pdsi  climate_pet  climate_pr  climate_ro  \
0                0           263         1195         206          10   
1                0           232         1196         201          10   
2                0           314         1190         192          10   
3                0           321         1144         186          66   
4                0           413         1187         186           9   
...            ...           ...          ...         ...         ...   
83143          324           142         1535         127           6   
83144          195           126         1490         136           7   
83145          272           111         1527         132           7   
83146          289            68         1510         128           6   
83147          436           125         1568         119           6   

       climate_soil  climate_srad  climate_swe  climate_tmmn  climate_tmmx  \
0              1692          1861            0           211           317   
1              1859          1867            0           211           318   
2              1677          1861            0           208           317   
3              1061          1864            0           196           303   
4              1714          1852            0           204           314   
...             ...           ...          ...           ...           ...   
83143            51          2233            0           206           319   
83144            61          2210            0           203           320   
83145            29          2205            0           211           333   
83146            62          2156            0           212           332   
83147             8          2192            0           219           345   

       climate_vap  climate_vpd  climate_vs   elevation  landcover_0  \
0             2493          111         141  413.474762          0.0   
1             2497          112         138  429.034543          0.0   
2             2486          109         141  477.246432          0.0   
3             2333           98         124  646.388681          0.0   
4             2426          109         145  582.340637          0.0   
...            ...          ...         ...         ...          ...   
83143         2111          148         223  464.141579          0.0   
83144         2156          143         206  402.388535          0.0   
83145         2225          160         198  366.349846          0.0   
83146         2258          155         208  293.380329          0.0   
83147         2292          177         197  265.379418          0.0   

       landcover_1  landcover_2  landcover_3  landcover_4  landcover_5  \
0              0.0     0.018654          0.0     0.714446     0.012174   
1              0.0     0.000000          0.0     0.654783     0.000095   
2              0.0     0.000000          0.0     0.516421     0.000000   
3              0.0     0.000000          0.0     0.299000     0.163902   
4              0.0     0.000000          0.0     0.277392     0.067742   
...            ...          ...          ..

In [6]:
# Display information of the train dataset
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 83148 entries, 0 to 83147
Data columns (total 29 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   ID             83148 non-null  object 
 1   lat            83148 non-null  float64
 2   lon            83148 non-null  float64
 3   burn_area      83148 non-null  float64
 4   climate_aet    83148 non-null  int64  
 5   climate_def    83148 non-null  int64  
 6   climate_pdsi   83148 non-null  int64  
 7   climate_pet    83148 non-null  int64  
 8   climate_pr     83148 non-null  int64  
 9   climate_ro     83148 non-null  int64  
 10  climate_soil   83148 non-null  int64  
 11  climate_srad   83148 non-null  int64  
 12  climate_swe    83148 non-null  int64  
 13  climate_tmmn   83148 non-null  int64  
 14  climate_tmmx   83148 non-null  int64  
 15  climate_vap    83148 non-null  int64  
 16  climate_vpd    83148 non-null  int64  
 17  climate_vs     83148 non-null  int64  
 18  elevat

In [7]:
train.isnull().sum()

ID               0
lat              0
lon              0
burn_area        0
climate_aet      0
climate_def      0
climate_pdsi     0
climate_pet      0
climate_pr       0
climate_ro       0
climate_soil     0
climate_srad     0
climate_swe      0
climate_tmmn     0
climate_tmmx     0
climate_vap      0
climate_vpd      0
climate_vs       0
elevation        0
landcover_0      0
landcover_1      0
landcover_2      0
landcover_3      0
landcover_4      0
landcover_5      0
landcover_6      0
landcover_7      0
landcover_8      0
precipitation    0
dtype: int64

In [8]:
train.describe()

lat           lon     burn_area   climate_aet   climate_def  \
count  83148.000000  83148.000000  83148.000000  83148.000000  83148.000000   
mean     -19.014557     29.860856      0.007632    484.491124    828.892721   
std        1.588444      1.751090      0.029226    470.467480    546.934469   
min      -22.358835     25.487029      0.000000      0.000000      0.000000   
25%      -20.358835     28.487029      0.000000     50.000000    375.000000   
50%      -18.858835     29.987029      0.000000    302.000000    858.000000   
75%      -17.858835     31.237029      0.000000    931.000000   1211.000000   
max      -15.858835     32.987029      0.843886   1713.000000   2614.000000   

       climate_pdsi   climate_pet    climate_pr    climate_ro  climate_soil  \
count  83148.000000  83148.000000  83148.000000  83148.000000  83148.000000   
mean     -30.806237   1313.382992     54.576322      6.215134    305.477919   
std      235.802930    315.209838     71.997561     21.480399    400.956123   
min     -563.000000    587.000000      0.000000      0.000000      1.000000   
25%     -212.000000   1081.000000      1.000000      0.000000     70.000000   
50%     -108.000000   1290.000000     22.000000      1.000000    149.000000   
75%      142.000000   1517.000000     87.000000      4.000000    329.000000   
max      851.000000   2620.000000    501.000000    342.000000   3319.000000   

       climate_srad  climate_swe  climate_tmmn  climate_tmmx   climate_vap  \
count  83148.000000      83148.0  83148.000000  83148.000000  83148.000000   
mean    2281.967901          0.0    140.830303    285.288654   1554.532123   
std      333.049616          0.0     44.631924     34.840502    458.461471   
min     1167.000000          0.0     19.000000    139.000000    704.000000   
25%     2028.000000          0.0    103.000000    262.000000   1139.000000   
50%     2272.000000          0.0    150.000000    287.000000   1544.000000   
75%     2545.000000          0.0    177.000000    310.000000   1942.000000   
max     3170.000000          0.0    244.000000    400.000000   2786.000000   

        climate_vpd    climate_vs     elevation   landcover_0   landcover_1  \
count  83148.000000  83148.000000  83148.000000  83148.000000  83148.000000   
mean     127.380117    208.414574    978.992612      0.006158      0.000017   
std       44.172381     47.550163    297.497348      0.053111      0.000141   
min       32.000000     48.000000    265.379418      0.000000      0.000000   
25%       97.000000    174.000000    768.375959      0.000000      0.000000   
50%      118.000000    205.000000   1022.813217      0.000000      0.000000   
75%      149.000000    241.000000   1197.977194      0.000000      0.000000   
max      344.000000    393.000000   1771.930689      0.828131      0.004918   

        landcover_2   landcover_3   landcover_4   landcover_5   landcover_6  \
count  83148.000000  8.314800e+04  83148.000000  83148.000000  83148.000000   
mean       0.008583  4.066313e-08      0.160628      0.037453      0.785382   
std        0.059046  3.535121e-06      0.192957      0.106050      0.233953   
min        0.000000  0.000000e+00      0.000000      0.000000      0.000019   
25%        0.000000  0.000000e+00      0.014993      0.000000      0.655322   
50%        0.000000  0.000000e+00      0.076706      0.000139      0.880600   
75%        0.000000  0.000000e+00      0.246498      0.015166      0.971209   
max        0.711603  3.073689e-04      0.981472      0.881323      1.000000   

        landcover_7   landcover_8  precipitation  
count  83148.000000  83148.000000   83148.000000  
mean       0.000354      0.001424       0.078551  
std        0.001773      0.014233       0.104464  
min        0.000000      0.000000       0.000000  
25%        0.000000      0.000000       0.002017  
50%        0.000000      0.000000       0.028503  
75%        0.000000      0.000000       0.125500  
max        0.016708      0.301823       0.801328

In [9]:
#drop all duplicates
train.drop_duplicates(inplace=True)

In [10]:
# Split the ID to get date string
train['date'] = pd.to_datetime(train['ID'].apply(lambda x: x.split('_')[1]))

In [11]:
# Extract year,month,day from datetime column
train['year'] = pd.to_datetime(train['date']).dt.year
train ['month'] = pd.to_datetime(train['date']).dt.month
train['day']=pd.to_datetime(train['date']).dt.day

In [12]:
train.nunique()

ID               83148
lat                 27
lon                 31
burn_area        16152
climate_aet       1584
climate_def       2348
climate_pdsi      1249
climate_pet       1779
climate_pr         420
climate_ro         272
climate_soil      2028
climate_srad      1781
climate_swe          1
climate_tmmn       219
climate_tmmx       254
climate_vap       1974
climate_vpd        308
climate_vs         327
elevation          533
landcover_0        229
landcover_1         65
landcover_2        774
landcover_3          2
landcover_4       6532
landcover_5       3053
landcover_6       6860
landcover_7        272
landcover_8        119
precipitation    80594
date               156
year                13
month               12
day                  1
dtype: int64

In [13]:
#drop date column and other columns with one value(day ,climate)
train.drop(columns=['day','date','climate_swe'],inplace=True)

In [14]:
train

ID        lat        lon  burn_area  climate_aet  \
0        0_2001-01-01 -15.858835  29.237029        0.0         1195   
1        1_2001-01-01 -15.858835  29.487029        0.0         1196   
2        2_2001-01-01 -15.858835  29.737029        0.0         1190   
3        3_2001-01-01 -15.858835  29.987029        0.0         1144   
4        4_2001-01-01 -15.858835  30.237029        0.0         1187   
...               ...        ...        ...        ...          ...   
83143  528_2013-12-01 -22.108835  30.737029        0.0         1210   
83144  529_2013-12-01 -22.108835  30.987029        0.0         1295   
83145  530_2013-12-01 -22.108835  31.237029        0.0         1254   
83146  531_2013-12-01 -22.108835  31.487029        0.0         1221   
83147  532_2013-12-01 -22.358835  31.237029        0.0         1132   

       climate_def  climate_pdsi  climate_pet  climate_pr  climate_ro  \
0                0           263         1195         206          10   
1                0           232         1196         201          10   
2                0           314         1190         192          10   
3                0           321         1144         186          66   
4                0           413         1187         186           9   
...            ...           ...          ...         ...         ...   
83143          324           142         1535         127           6   
83144          195           126         1490         136           7   
83145          272           111         1527         132           7   
83146          289            68         1510         128           6   
83147          436           125         1568         119           6   

       climate_soil  climate_srad  climate_tmmn  climate_tmmx  climate_vap  \
0              1692          1861           211           317         2493   
1              1859          1867           211           318         2497   
2              1677          1861           208           317         2486   
3              1061          1864           196           303         2333   
4              1714          1852           204           314         2426   
...             ...           ...           ...           ...          ...   
83143            51          2233           206           319         2111   
83144            61          2210           203           320         2156   
83145            29          2205           211           333         2225   
83146            62          2156           212           332         2258   
83147             8          2192           219           345         2292   

       climate_vpd  climate_vs   elevation  landcover_0  landcover_1  \
0              111         141  413.474762          0.0          0.0   
1              112         138  429.034543          0.0          0.0   
2              109         141  477.246432          0.0          0.0   
3               98         124  646.388681          0.0          0.0   
4              109         145  582.340637          0.0          0.0   
...            ...         ...         ...          ...          ...   
83143          148         223  464.141579          0.0          0.0   
83144          143         206  402.388535          0.0          0.0   
83145          160         198  366.349846          0.0          0.0   
83146          155         208  293.380329          0.0          0.0   
83147          177         197  265.379418          0.0          0.0   

       landcover_2  landcover_3  landcover_4  landcover_5  landcover_6  \
0         0.018654          0.0     0.714446     0.012174     0.244890   
1         0.000000          0.0     0.654783     0.000095     0.345121   
2         0.000000          0.0     0.516421     0.000000     0.483579   
3         0.000000          0.0     0.299000     0.163902     0.537098   
4         0.000000          0.0     0.277392     0.067742     0.654866   
...            ...          ...          ..

In [15]:
test=pd.read_csv('/content/drive/MyDrive/fire-extent-prediction-challenge-120240716-19716-ztmgh3/Test.csv')
test

ID        lat        lon  climate_aet  climate_def  \
0        0_2014-01-01 -15.858835  29.237029         1146           74   
1        1_2014-01-01 -15.858835  29.487029         1118           98   
2        2_2014-01-01 -15.858835  29.737029         1067          137   
3        3_2014-01-01 -15.858835  29.987029          969          187   
4        4_2014-01-01 -15.858835  30.237029          927          270   
...               ...        ...        ...          ...          ...   
25579  528_2017-12-01 -22.108835  30.737029          802         1030   
25580  529_2017-12-01 -22.108835  30.987029          819          971   
25581  530_2017-12-01 -22.108835  31.237029          756         1076   
25582  531_2017-12-01 -22.108835  31.487029          749         1071   
25583  532_2017-12-01 -22.358835  31.237029          609         1283   

       climate_pdsi  climate_pet  climate_pr  climate_ro  climate_soil  \
0              -451         1220         120           6           212   
1              -405         1216         117           6           330   
2              -468         1204         111           6           194   
3              -533         1156         101           5            78   
4              -505         1197          96           5           139   
...             ...          ...         ...         ...           ...   
25579           168         1832          84           4            81   
25580           169         1790          85           4            81   
25581           156         1833          79           4            88   
25582           178         1820          78           4           102   
25583          -118         1892          64           3            57   

       climate_srad  climate_swe  climate_tmmn  climate_tmmx  climate_vap  \
0              1974            0           217           303         2481   
1              1973            0           216           304         2481   
2              1958            0           214           302         2465   
3              1954            0           202           290         2317   
4              1939            0           210           301         2412   
...             ...          ...           ...           ...          ...   
25579          2757            0           202           328         1958   
25580          2725            0           199           330         1980   
25581          2710            0           208           343         2021   
25582          2653            0           210           342         2051   
25583          2704            0           217           355         2049   

       climate_vpd  climate_vs   elevation  landcover_0  landcover_1  \
0               99         148  413.474762          0.0     0.000615   
1              100         143  429.034543          0.0     0.000000   
2               97         143  477.246432          0.0     0.000000   
3               88         122  646.388681          0.0     0.000000   
4               99         143  582.340637          0.0     0.000000   
...            ...         ...         ...          ...          ...   
25579          173         239  464.141579          0.0     0.000000   
25580          172         221  402.388535          0.0     0.000000   
25581          194         213  366.349846          0.0     0.000000   
25582          190         223  293.380329          0.0     0.000000   
25583          217         214  265.379418          0.0     0.000000   

       landcover_2  landcover_3  landcover_4  landcover_5  landcover_6  \
0         0.015418          0.0     0.416704     0.023724     0.530016   
1         0.000000          0.0     0.406436     0.000446     0.593118   
2         0.000000          0.0     0.254791     0.000000     0.745209   
3         0.000000          0.0     0.219340     0.182153     0.598507   
4         0.000000          0.0     0.220239     0.097748     0.682013   
...            ... 

In [16]:
test.drop_duplicates(inplace=True)

In [17]:
# Split the ID to get the date string
test['date'] = pd.to_datetime(test['ID'].apply(lambda x: x.split('_')[1]))

In [18]:
#extract year,month,day from datetime column
test['year'] = pd.to_datetime(test['date']).dt.year
test['month'] = pd.to_datetime(test['date']).dt.month
test['day']=pd.to_datetime(test['date']).dt.day

In [19]:
test.nunique()

ID               25584
lat                 27
lon                 31
climate_aet       1626
climate_def       2248
climate_pdsi      1990
climate_pet       1701
climate_pr         473
climate_ro         340
climate_soil      1754
climate_srad      1447
climate_swe          1
climate_tmmn       214
climate_tmmx       240
climate_vap       1958
climate_vpd        346
climate_vs         291
elevation          533
landcover_0        111
landcover_1         36
landcover_2        249
landcover_3          2
landcover_4       2444
landcover_5       1246
landcover_6       2534
landcover_7        139
landcover_8         81
precipitation    23615
date                48
year                 4
month               12
day                  1
dtype: int64

In [20]:
#drop date column and other columns with one value(day ,climate)
test.drop(columns=['day','date','climate_swe'],inplace=True)

In [21]:
test

ID        lat        lon  climate_aet  climate_def  \
0        0_2014-01-01 -15.858835  29.237029         1146           74   
1        1_2014-01-01 -15.858835  29.487029         1118           98   
2        2_2014-01-01 -15.858835  29.737029         1067          137   
3        3_2014-01-01 -15.858835  29.987029          969          187   
4        4_2014-01-01 -15.858835  30.237029          927          270   
...               ...        ...        ...          ...          ...   
25579  528_2017-12-01 -22.108835  30.737029          802         1030   
25580  529_2017-12-01 -22.108835  30.987029          819          971   
25581  530_2017-12-01 -22.108835  31.237029          756         1076   
25582  531_2017-12-01 -22.108835  31.487029          749         1071   
25583  532_2017-12-01 -22.358835  31.237029          609         1283   

       climate_pdsi  climate_pet  climate_pr  climate_ro  climate_soil  \
0              -451         1220         120           6           212   
1              -405         1216         117           6           330   
2              -468         1204         111           6           194   
3              -533         1156         101           5            78   
4              -505         1197          96           5           139   
...             ...          ...         ...         ...           ...   
25579           168         1832          84           4            81   
25580           169         1790          85           4            81   
25581           156         1833          79           4            88   
25582           178         1820          78           4           102   
25583          -118         1892          64           3            57   

       climate_srad  climate_tmmn  climate_tmmx  climate_vap  climate_vpd  \
0              1974           217           303         2481           99   
1              1973           216           304         2481          100   
2              1958           214           302         2465           97   
3              1954           202           290         2317           88   
4              1939           210           301         2412           99   
...             ...           ...           ...          ...          ...   
25579          2757           202           328         1958          173   
25580          2725           199           330         1980          172   
25581          2710           208           343         2021          194   
25582          2653           210           342         2051          190   
25583          2704           217           355         2049          217   

       climate_vs   elevation  landcover_0  landcover_1  landcover_2  \
0             148  413.474762          0.0     0.000615     0.015418   
1             143  429.034543          0.0     0.000000     0.000000   
2             143  477.246432          0.0     0.000000     0.000000   
3             122  646.388681          0.0     0.000000     0.000000   
4             143  582.340637          0.0     0.000000     0.000000   
...           ...         ...          ...          ...          ...   
25579         239  464.141579          0.0     0.000000     0.000000   
25580         221  402.388535          0.0     0.000000     0.000000   
25581         213  366.349846          0.0     0.000000     0.000000   
25582         223  293.380329          0.0     0.000000     0.000000   
25583         214  265.379418          0.0     0.000000     0.000000   

       landcover_3  landcover_4  landcover_5  landcover_6  landcover_7  \
0              0.0     0.416704     0.023724     0.530016     0.013524   
1              0.0     0.406436     0.000446     0.593118     0.000000   
2              0.0     0.254791     0.000000     0.745209     0.000000   
3              0.0     0.219340     0.182153     0.598507     0.000000   
4              0.0     0.220239     0.097748     0.682013     0.000000   
...            ... 

model building

In [22]:
# Features to use
train_features = ['lat','lon','climate_aet','climate_def','climate_pdsi','climate_pet','climate_pr','climate_ro',
                   'climate_soil','climate_srad','climate_tmmn','climate_tmmx','climate_vap','climate_vpd',
                   'climate_vs','elevation','landcover_0','landcover_1','landcover_2','landcover_3','landcover_4',
                   'landcover_5','landcover_6','landcover_7','landcover_8','precipitation','year','month']

In [23]:
# Define features and target variable
X_train = train[train_features]
y_train = train['burn_area']
X_test = test[train_features]

In [24]:
# Scale the features
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

In [25]:
# Feature Selection with RFE
xgb = XGBRegressor(random_state=42)
selector = RFECV(estimator=xgb, step=1, cv=5)
selector = selector.fit(X_train_scaled, y_train)
X_train_selected = selector.transform(X_train_scaled)
X_test_selected = selector.transform(X_test_scaled)

In [26]:
# Initialize XGBoost model
xgb = XGBRegressor(random_state=42)

In [27]:
# param_grid = {
#     'n_estimators': [100, 200, 300],
#     'max_depth': [None, 10, 20, 30],
#     'min_samples_split': [2, 5, 10],
#     'min_samples_leaf': [1, 2, 4]
# }

# grid_search = GridSearchCV(estimator=model, param_grid=param_grid, cv=3, n_jobs=-1, verbose=2)
# grid_search.fit(X_train, y_train)

In [28]:

#Define parameter grid for GridSearchCV
param_grid = {'n_estimators': [100, 200, 300],
                       'max_depth': [3, 5, 7, 10],
                       'learning_rate': [0.01, 0.1, 0.2],
                       'subsample': [0.8, 0.9, 1.0],
                       'colsample_bytree': [0.8, 0.9, 1.0]}

In [29]:
# Perform Grid Search with Cross-Validation
grid_search = GridSearchCV(estimator=xgb, param_grid=param_grid, scoring='neg_mean_squared_error',n_jobs=-1, verbose=2)
grid_search.fit(X_train_selected, y_train)

# Best parameters from Grid Search
print(f"Best Parameters: {grid_search.best_params_}")

Fitting 5 folds for each of 324 candidates, totalling 1620 fits
Best Parameters: {'colsample_bytree': 0.8, 'learning_rate': 0.2, 'max_depth': 7, 'n_estimators': 200, 'subsample': 1.0}


In [30]:
# Train the model with the best parameters
best_model = grid_search.best_estimator_
best_model.fit(X_train_selected, y_train)

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=0.8, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=0.2, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=7, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy=None, n_estimators=200, n_jobs=None,
             num_parallel_tree=None, random_state=42, ...)

In [31]:
# Evaluate on the validation set
val_predictions = best_model.predict(X_train_selected)
val_mse = mean_squared_error(y_train, val_predictions)
rmse = mean_squared_error(y_train, val_predictions,squared=False)
val_r2 = r2_score(y_train, val_predictions)

In [32]:
print(f"Training rmse: {rmse}")

Training rmse: 0.02035244294567497


In [33]:
print(f"Training Mean Squared Error: {val_mse}")
print(f"Training R^2 Score: {val_r2}")

Training Mean Squared Error: 0.00041422193385695486
Training R^2 Score: 0.5150493817938411


In [34]:
# Make predictions on the test set
test_predictions = best_model.predict(X_test_selected)

In [35]:
# Prepare the submission file
submission = pd.DataFrame({
    'ID': test['ID'],
    'burn_area': test_predictions
})
submission.to_csv('submission.csv', index=False)

In [36]:
pd.set_option('display.max_row', None)
submission

ID     burn_area
0        0_2014-01-01  2.177294e-04
1        1_2014-01-01 -5.695627e-04
2        2_2014-01-01  5.900940e-04
3        3_2014-01-01 -1.516400e-04
4        4_2014-01-01  3.202027e-04
5        5_2014-01-01  4.805573e-04
6        6_2014-01-01  2.130142e-03
7        7_2014-01-01  1.473830e-03
8        8_2014-01-01 -4.977161e-04
9        9_2014-01-01 -1.843375e-04
10      10_2014-01-01 -1.101394e-04
11      11_2014-01-01 -5.285514e-05
12      12_2014-01-01  9.485749e-04
13      13_2014-01-01 -4.683750e-05
14      14_2014-01-01 -1.135753e-04
15      15_2014-01-01  1.124319e-03
16      16_2014-01-01  1.593099e-03
17      17_2014-01-01 -5.559924e-04
18      18_2014-01-01 -1.850091e-03
19      19_2014-01-01 -6.962234e-04
20      20_2014-01-01 -1.472816e-03
21      21_2014-01-01 -4.463206e-04
22      22_2014-01-01 -3.930434e-04
23      23_2014-01-01  2.280461e-04
24      24_2014-01-01 -3.863155e-04
25      25_2014-01-01  8.321315e-04
26      26_2014-01-01  3.634416e-04
27      27_2014-01-01 -4.570313e-04
28      28_2014-01-01 -9.556226e-05
29      29_2014-01-01  1.577875e-03
30      30_2014-01-01  2.631203e-04
31      31_2014-01-01 -4.663908e-04
32      32_2014-01-01 -8.017952e-06
33      33_2014-01-01  8.310071e-04
34      34_2014-01-01 -7.500343e-04
35      35_2014-01-01 -5.607471e-04
36      36_2014-01-01  5.359086e-04
37      37_2014-01-01  1.672892e-04
38      38_2014-01-01  4.059843e-04
39      39_2014-01-01 -1.028790e-03
40      40_2014-01-01 -5.143556e-04
41      41_2014-01-01 -7.614217e-04
42      42_2014-01-01  3.943428e-04
43      43_2014-01-01  2.266750e-05
44      44_2014-01-01 -6.554099e-04
45      45_2014-01-01  9.127066e-04
46      46_2014-01-01  1.386583e-03
47      47_2014-01-01 -1.388841e-03
48      48_2014-01-01 -2.475496e-04
49      49_2014-01-01  1.112310e-03
50      50_2014-01-01 -9.475722e-04
51      51_2014-01-01  3.754441e-04
52      52_2014-01-01  1.619474e-04
53      53_2014-01-01 -1.972743e-04
54      54_2014-01-01  1.884313e-04
55      55_2014-01-01 -4.517433e-04
56      56_2014-01-01 -4.960469e-04
57      57_2014-01-01  4.780395e-04
58      58_2014-01-01  1.016379e-03
59      59_2014-01-01  3.105243e-04
60      60_2014-01-01  1.677921e-04
61      61_2014-01-01 -1.980543e-04
62      62_2014-01-01  1.384252e-04
63      63_2014-01-01 -2.946966e-04
64      64_2014-01-01 -7.296421e-04
65      65_2014-01-01  1.309477e-03
66      66_2014-01-01  1.192625e-03
67      67_2014-01-01 -4.875980e-04
68      68_2014-01-01 -1.336249e-03
69      69_2014-01-01  5.634654e-04
70      70_2014-01-01  2.116925e-05
71      71_2014-01-01  6.394485e-04
72      72_2014-01-01 -1.718968e-03
73      73_2014-01-01  1.378586e-03
74      74_2014-01-01 -3.152698e-04
75      75_2014-01-01 -5.375360e-04
76      76_2014-01-01  6.869148e-04
77      77_2014-01-01 -1.128024e-03
78      78_2014-01-01  4.856227e-04
79      79_2014-01-01 -5.367505e-04
80      80_2014-01-01 -9.094151e-05
81      81_2014-01-01 -2.140732e-04
82      82_2014-01-01 -1.355962e-04
83      83_2014-01-01 -1.469055e-04
84      84_2014-01-01 -5.353491e-04
85      85_2014-01-01  6.048626e-04
86      86_2014-01-01  5.419026e-05
87      87_2014-01-01 -8.554196e-04
88      88_2014-01-01 -3.073571e-04
89      89_2014-01-01  3.355787e-04
90      90_2014-01-01  1.683337e-04
91      91_2014-01-01 -7.606983e-04
92      92_2014-01-01  1.363016e-03
93      93_2014-01-01  1.023187e-03
94      94_2014-01-01  1.437402e-03
95      95_2014-01-01  9.389066e-05
96      96_2014-01-01  6.945101e-06
97      97_2014-01-01 -3.132617e-04
98      98_2014-01-01  1.115946e-03
99      99_2014-01-01  1.342694e-04
100    100_2014-01-01 -1.262660e-03
101    101_2014-01-01 -6.446670e-05
102    102_2014-01-01 -7.736836e-05
103    103_2014-01-01  5.360188e-04
104    104_2014-01-01  2.516220e-04
105    105_2014-01-01  8.034046e-05
106    106_2014-01-01 -4.792818e-04
107    107_2014-01-01  1.506130e-03
108    108_2014-01-01 -6.352074e-04
109    109_2014-01-01  2.280199e-05
110    110_2014-01-01 -